In [2]:
from policyengine_core.model_api import *
from policyengine_us import *
from scipy.optimize import differential_evolution

INCOME_ELASTICITY = -0.05
SUBSTITUTION_ELASTICITY = 0.25

def create_funding_reform(flat_tax_rate: float, include_lsrs: bool = True):
    return Reform.from_dict({
        "gov.contrib.ubi_center.flat_tax.abolish_federal_income_tax": {
            "year:2023:10": True
        },
        "gov.contrib.ubi_center.flat_tax.abolish_payroll_tax": {
            "year:2023:10": True
        },
        "gov.contrib.ubi_center.flat_tax.abolish_self_emp_tax": {
            "year:2023:10": True
        },
        "gov.ssa.ssi.abolish_ssi": {
            "year:2023:10": True
        },
        "gov.usda.snap.abolish_snap": {
            "year:2023:10": True
        },
        "gov.usda.wic.abolish_wic": {
            "year:2023:10": True
        },
        "gov.contrib.ubi_center.flat_tax.rate": {
            "year:2023:10": flat_tax_rate
        },
        "gov.contrib.ubi_center.flat_tax.deduct_ptc": {
            "year:2023:10": True
        },
        "gov.usda.snap.emergency_allotment.allowed": {
            "year:2023:10": False
        },
        "simulation.reported_state_income_tax": {
            "year:2023:10": True
        },
        "gov.simulation.labor_supply_responses.income_elasticity": {
            "year:2023:10": INCOME_ELASTICITY
        } if include_lsrs else {},
        "gov.simulation.labor_supply_responses.substitution_elasticity": {
            "year:2023:10": SUBSTITUTION_ELASTICITY
        } if include_lsrs else {},
    },
    "us",
    )

def create_baseline_reform():
    return Reform.from_dict({
            "gov.usda.snap.emergency_allotment.allowed": {
                "year:2023:10": False
            },
            "simulation.reported_state_income_tax": {
                "year:2023:10": True
            },
        },
        "us",
    )

baseline = Microsimulation(reform=create_baseline_reform(), dataset="enhanced_cps_2023")

class BlankSlatePolicy:
    young_child: float = 0
    older_child: float = 0
    young_adult: float = 0
    adult: float = 0
    senior: float = 0
    flat_tax_rate: float = 0.40

    def __init__(self, flat_tax_rate: float = 0.40, year: int = 2023, include_lsrs: bool = True):
        self.baseline = baseline
        self.blank_slate_funded = Microsimulation(reform=create_funding_reform(flat_tax_rate, include_lsrs), dataset="enhanced_cps_2023")
        self.baseline.default_calculation_period = year
        self.blank_slate_funded.default_calculation_period = year
        self.df = self.create_dataframe()
        self.ubi_funding = self.get_ubi_funding()
        self.flat_tax_rate = flat_tax_rate
        self.include_lsrs = include_lsrs

    def create_dataframe(self) -> pd.DataFrame:
        age = self.baseline.calc("age").values
        df = pd.DataFrame(
            dict(
                baseline_net_income=self.baseline.calc(
                    "household_net_income"
                ).values,
                baseline_tax=self.baseline.calculate(
                    "household_tax"
                ).values,
                baseline_benefits=self.baseline.calculate(
                    "household_benefits"
                ).values,
                count_young_child=self.baseline.map_result(
                    age < 6, "person", "household"
                ),
                count_older_child=self.baseline.map_result(
                    (age >= 6) & (age < 18), "person", "household"
                ),
                count_adult=self.baseline.map_result(
                    (age >= 18) & (age < 65), "person", "household"
                ),
                count_senior=self.baseline.map_result(
                    age >= 65, "person", "household"
                ),
                count_person=self.baseline.map_result(
                    age >= 0, "person", "household"
                ),
                funded_net_income=self.blank_slate_funded.calculate(
                    "household_net_income"
                ).values,
                funded_tax=self.blank_slate_funded.calculate(
                    "household_tax"
                ).values,
                funded_benefits=self.blank_slate_funded.calculate(
                    "household_benefits"
                ).values,
                count_disabled=self.baseline.calculate("is_ssi_disabled", map_to="household").values,
                weight=self.baseline.calculate("household_weight").values,
            )
        )

        df["total_employment_income"] = self.baseline.calculate("employment_income", map_to="household").values
        return df

    def get_ubi_funding(self) -> float:
        return (
            (self.df.funded_tax - self.df.funded_benefits - self.df.baseline_tax + self.df.baseline_benefits)
            * self.df.weight
        ).sum()

    def get_senior_amount(
        self,
        young_child: float,
        older_child: float,
        adult: float,
        disabled: float,
        funding_offset: float = 0,
    ) -> float:
        return (
            self.ubi_funding - funding_offset
            - young_child * (self.df.count_young_child * self.df.weight).sum()
            - older_child * (self.df.count_older_child * self.df.weight).sum()
            - adult * (self.df.count_adult * self.df.weight).sum()
            - disabled * (self.df.count_disabled * self.df.weight).sum()
        ) / (self.df.count_senior * self.df.weight).sum()

    def mean_percentage_loss(
        self,
        young_child: float,
        older_child: float,
        adult: float,
        disabled: float,
        return_extras: bool = False
    ) -> float:
        senior_amount = self.get_senior_amount(
            young_child, older_child, adult, disabled,
        )
        final_net_income = (
            self.df.funded_net_income
            + self.df.count_young_child * young_child
            + self.df.count_older_child * older_child
            + self.df.count_adult * adult
            + self.df.count_senior * senior_amount
            + self.df.count_disabled * disabled
        )
        gain = final_net_income - self.df.baseline_net_income
        income_rel_change = final_net_income / self.df.funded_net_income - 1
        income_rel_change_c = np.clip(income_rel_change, -1, 1)
        income_effect = income_rel_change_c * self.df.total_employment_income * INCOME_ELASTICITY
        employment_income_change = income_effect
        MTR_GUESS = 0.3
        rough_net_income_change_from_lsr = employment_income_change * (1 - MTR_GUESS)
        rough_tax_change_from_lsr = employment_income_change * MTR_GUESS
        total_ubi_funding_change = (rough_tax_change_from_lsr * self.df.weight).sum()
        if self.include_lsrs:
            senior_amount = self.get_senior_amount(
                young_child, older_child, adult, disabled, total_ubi_funding_change
            )
        final_net_income = (
            self.df.funded_net_income
            + self.df.count_young_child * young_child
            + self.df.count_older_child * older_child
            + self.df.count_adult * adult
            + self.df.count_senior * senior_amount
            + self.df.count_disabled * disabled
        )
        gain = final_net_income - self.df.baseline_net_income + rough_net_income_change_from_lsr
        if not self.include_lsrs:
            gain = gain - rough_net_income_change_from_lsr
        absolute_loss = np.maximum(0, -gain)
        pct_loss = absolute_loss / np.maximum(100, self.df.baseline_net_income)
        average = np.average(
            pct_loss, weights=self.df.weight * self.df.count_person
        )
        if return_extras:
            return average, senior_amount, total_ubi_funding_change
        return average

    def solve(self, return_amounts: bool = False, return_loss: bool = False) -> dict:
        (
            self.young_child,
            self.older_child,
            self.adult,
            self.disabled,
        ) = differential_evolution(
            lambda x: self.mean_percentage_loss(*x),
            bounds=[(0, 30e3 * self.flat_tax_rate)] * 4,
            maxiter=int(1e2),
            seed=0,
        ).x
        _, self.senior, _ = self.mean_percentage_loss(
            self.young_child, self.older_child, self.adult, self.disabled, return_extras=True
        )
        self.reform = Reform.from_dict(
            {
                **create_funding_reform(self.flat_tax_rate).parameter_values,
                "gov.contrib.ubi_center.basic_income.amount.person.by_age[0].amount": {
                    "year:2023:10": self.young_child
                },
                "gov.contrib.ubi_center.basic_income.amount.person.by_age[1].amount": {
                    "year:2023:10": self.older_child
                },
                "gov.contrib.ubi_center.basic_income.amount.person.by_age[2].amount": {
                    "year:2023:10": self.adult
                },
                "gov.contrib.ubi_center.basic_income.amount.person.by_age[3].amount": {
                    "year:2023:10": self.adult
                },
                "gov.contrib.ubi_center.basic_income.amount.person.by_age[4].amount": {
                    "year:2023:10": self.senior
                },
                "gov.contrib.ubi_center.basic_income.amount.person.disability": {
                    "year:2023:10": self.disabled
                },
            },
            "us",
        )
        if not return_amounts and not return_loss:
            return self.reform
        
        data = dict(reform=self.reform)

        if return_amounts:
            data["amounts"] = dict(
                young_child=self.young_child,
                older_child=self.older_child,
                adult=self.adult,
                senior=self.senior,
                disabled=self.disabled,
            )
        
        if return_loss:
            data["loss"] = self.mean_percentage_loss(
                self.young_child, self.older_child, self.adult, self.disabled
            )
        
        public_reform = Reform.from_dict(
            {
                path: value for path, value in self.reform.parameter_values.items()
                if path.startswith("gov")
            },
            "us",
        )
        data["id"] = public_reform.api_id
        data["reform"] = public_reform
        
        return data

In [3]:
policy_2024 = BlankSlatePolicy(0.34, year=2024)
data_2024 = policy_2024.solve(return_amounts=True, return_loss=True)

In [6]:
policy_2024 = BlankSlatePolicy(0.29, year=2024)
data_2024 = policy_2024.solve(return_amounts=True, return_loss=True)

In [8]:
data_2024

{'reform': policyengine_core.reforms.reform.Reform.from_dict.<locals>.reform,
 'amounts': {'young_child': 3796.9693787325014,
  'older_child': 2799.6852762886547,
  'adult': 3910.449886241183,
  'senior': 3168.354941369422,
  'disabled': 3708.8509442687473},
 'loss': 0.04685237119436781,
 'id': 42517}

In [10]:
import plotly.express as px
from policyengine_core.charts import *
from tqdm import tqdm

tax_rates = []
losses = []
api_ids = []

for flat_tax_rate in tqdm(np.linspace(0.2, 0.4, 21)):
    policy = BlankSlatePolicy(flat_tax_rate, year=2024)
    data = policy.solve(return_amounts=True, return_loss=True)
    tax_rates.append(flat_tax_rate)
    losses.append(data["loss"])
    api_ids.append(data["id"])

df = pd.DataFrame(dict(
    flat_tax_rate=tax_rates,
    loss=losses,
    api_id=api_ids,
))

fig = px.line(
    df.sort_values("flat_tax_rate"),
    x="flat_tax_rate",
    y="loss",
)


format_fig(fig).update_traces(
    # Set color to BLUE
    line=dict(color=BLUE_PRIMARY),
).update_layout(
    title="Mean percentage loss by flat tax rate",
    xaxis_title="Flat tax rate",
    yaxis_title="Loss",
    xaxis_tickformat=".0%",
    yaxis_tickformat=".1%",
)

100%|██████████| 21/21 [1:14:40<00:00, 213.35s/it]


In [ ]:
from policyengine_us import Microsimulation
from policyengine_core.reforms import Reform
from policyengine_core.periods import instant
import pandas as pd


def modify_parameters(parameters):
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[0].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["young_child"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[1].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["older_child"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[2].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["young_adult"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[3].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["adult"])
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[4].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=data["amounts"]["senior"])
    parameters.gov.contrib.ubi_center.flat_tax.abolish_federal_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_payroll_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_self_emp_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.deduct_ptc.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.rate.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=0.3)
    parameters.gov.simulation.labor_supply_responses.income_elasticity.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=-0.05)
    parameters.gov.simulation.labor_supply_responses.substitution_elasticity.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=0.25)
    parameters.gov.ssa.ssi.abolish_ssi.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.usda.snap.abolish_snap.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.usda.snap.emergency_allotment.allowed.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=False)
    parameters.gov.usda.wic.abolish_wic.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.simulation.reported_state_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    return parameters

class bs_reform(Reform):
    def apply(self):
        self.modify_parameters(modify_parameters)


def baseline_modify_parameters(parameters):
    parameters.simulation.reported_state_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    return parameters

class baseline_reform(Reform):
    def apply(self):
        self.modify_parameters(baseline_modify_parameters)


baseline = Microsimulation(reform=baseline_reform, dataset="enhanced_cps_2023")
reformed = Microsimulation(reform=bs_reform, dataset="enhanced_cps_2023")

In [ ]:
data["reform"].api_id

42318

In [ ]:
reform_pos = reformed.calculate("household_tax").sum()/1e9 - reformed.calculate("household_benefits").sum()/1e9
baseline_pos = baseline.calculate("household_tax").sum()/1e9 - baseline.calculate("household_benefits").sum()/1e9
reform_pos - baseline_pos

-14.265113360794203

In [ ]:
policy.blank_slate_funded.calculate("household_tax").sum()/1e9 - policy.baseline.calculate("household_benefits").sum()/1e9

3082.306692309179

In [ ]:
from policyengine_us import Simulation
from policyengine_core.reforms import Reform
from policyengine_core.periods import instant
import pandas as pd


def modify_parameters(parameters):
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[0].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=3871.303409123619)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[1].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=2748.040844692595)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[2].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=4222.691573142556)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[3].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=4407.959357095953)
    parameters.gov.contrib.ubi_center.basic_income.amount.person.by_age[4].amount.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=3574.607933975744)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_federal_income_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_payroll_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.abolish_self_emp_tax.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.deduct_ptc.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.contrib.ubi_center.flat_tax.rate.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=0.3)
    parameters.gov.simulation.labor_supply_responses.income_elasticity.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=-0.05)
    parameters.gov.simulation.labor_supply_responses.substitution_elasticity.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=0.25)
    parameters.gov.ssa.ssi.abolish_ssi.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.usda.snap.abolish_snap.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    parameters.gov.usda.snap.emergency_allotment.allowed.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=False)
    parameters.gov.usda.wic.abolish_wic.update(start=instant("2023-01-01"), stop=instant("2032-12-31"), value=True)
    return parameters


class reform(Reform):
    def apply(self):
        self.modify_parameters(modify_parameters)


situation = {
  "families": {
    "your family": {
      "members": [
        "you"
      ]
    }
  },
  "households": {
    "your household": {
      "members": [
        "you"
      ]
    }
  },
  "marital_units": {
    "your marital unit": {
      "members": [
        "you"
      ]
    }
  },
  "people": {
    "you": {
      "age": {
        "2023": 40
      },
      "employment_income": {
        "2023": 500000
      }
    }
  },
  "spm_units": {
    "your household": {
      "members": [
        "you"
      ]
    }
  },
  "tax_units": {
    "your tax unit": {
      "members": [
        "you"
      ]
    }
  }
}

simulation = Simulation(
    reform=reform,
    situation=situation,
)

simulation.trace = True
simulation.calculate("employment_income", 2023)

array([516497.25], dtype=float32)

In [ ]:
simulation.tracer.print_computation_log(max_depth=6)

  employment_income<2023, (default)> = [516497.25]
    employment_income_before_lsr<2023, (default)> = [500000.]
    employment_income_behavioral_response<2023, (default)> = [16497.266]
      income_elasticity_lsr<2023, (default)> = [-1394.6615]
        employment_income_before_lsr<2023, (default)> = [500000.]
        relative_income_change<2023, (default)> = [0.05578646]
          household_net_income<2023, (lsr_measurement)> = [309192.34]
            household_market_income<2023, (lsr_measurement)> = [500000.]
            household_benefits<2023, (lsr_measurement)> = [4407.9595]
            household_refundable_tax_credits<2023, (lsr_measurement)> = [0.]
            household_tax_before_refundable_credits<2023, (lsr_measurement)> = [195215.62]
      substitution_elasticity_lsr<2023, (default)> = [17891.928]
        employment_income_before_lsr<2023, (default)> = [500000.]
        relative_wage_change<2023, (default)> = [0.14313543]
          marginal_tax_rate<2023, (lsr_measurement)>

In [ ]:
px.bar(
    reformed.calculate("employment_income_behavioral_response").groupby(reformed.calculate("income_decile", map_to="person")).sum()
)

In [ ]:
import plotly.express as px

res = reformed.calculate("employment_income_behavioral_response")

px.histogram(
    res.clip(res.quantile(0.01), res.quantile(0.99)),
    nbins=100,
)

In [ ]:
tax_change = reformed.calculate("household_tax").sum()/1e9 - baseline.calculate("household_tax").sum()/1e9
flat_tax_revenue = reformed.calculate("flat_tax").sum()/1e9
benefit_change = reformed.calculate("household_benefits").sum()/1e9 - baseline.calculate("household_benefits").sum()/1e9
basic_income_payments = reformed.calculate("basic_income").sum()/1e9

tax_abolition_budgetary_impact = tax_change - flat_tax_revenue
benefit_abolition_budgetary_impact = -(benefit_change - basic_income_payments)

flat_tax_revenue_budgetary_impact = flat_tax_revenue
basic_income_payments_budgetary_impact = -basic_income_payments

[tax_abolition_budgetary_impact, benefit_abolition_budgetary_impact, flat_tax_revenue_budgetary_impact, basic_income_payments_budgetary_impact]

[-3236.3256686219, 206.62841945258106, 1508.9800102127294, -1315.0695297194302]